In [1]:
#install packages
!pip install tpot
!pip install mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 3.3 MB/s 
     |████████████████████████████████| 139 kB 10.9 MB/s 
     |████████████████████████████████| 255.9 MB 39 kB/s 
  Created wheel for stopit: filename=stopit-1.1.2-py3-none-any.whl size=11954 sha256=c921001680fbb495003520683c183445f01f777b4a7c7c08ad11cdffe11cb6e3
  Stored in directory: /root/.cache/pip/wheels/e2/d2/79/eaf81edb391e27c87f51b8ef901ecc85a5363dc96b8b8d71e3
Successfully built stopit
  Attempting uninstall: xgboost
    Found existing installation: xgboost 0.90
    Uninstalling xgboost-0.90:
      Successfully uninstalled xgboost-0.90
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 112 kB 5.2 MB/s 
     |████████████████████████████████| 2.0 MB 37.0 MB/s 
     |████████████████████████████████| 76.6 MB 1.3 MB/s 
     |███████████████

In [4]:
#import dependencies
import pandas as pd
import tpot as tpot
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from supervised.automl import AutoML

In [29]:
#import SPARCS data
df = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
df

Health Service Area Hospital County  ...  Total Charges  Total Costs
0              Western NY        Allegany  ...        4757.01      4747.83
1              Western NY        Allegany  ...        5090.25      2985.64
2              Western NY        Allegany  ...        4948.50      2129.67
3              Western NY        Allegany  ...        4719.75      8454.41
4              Western NY        Allegany  ...       50384.75     34565.03
...                   ...             ...  ...            ...          ...
23578         Long Island         Suffolk  ...       50833.00      8961.40
23579         Long Island         Suffolk  ...       10948.00      2214.06
23580         Long Island         Suffolk  ...       46421.00     11083.24
23581         Long Island         Suffolk  ...       46122.00      7951.26
23582         Long Island         Suffolk  ...       32225.00      6212.95

[23583 rows x 34 columns]

In [27]:
df.dtypes

Health Service Area                     object
Hospital County                         object
Operating Certificate Number           float64
Facility Id                            float64
Facility Name                           object
Age Group                               object
Zip Code - 3 digits                     object
Gender                                  object
Race                                    object
Ethnicity                               object
Length of Stay                          object
Type of Admission                       object
Patient Disposition                     object
Discharge Year                           int64
CCS Diagnosis Code                       int64
CCS Diagnosis Description               object
CCS Procedure Code                       int64
CCS Procedure Description               object
APR DRG Code                             int64
APR DRG Description                     object
APR MDC Code                             int64
APR MDC Descr

Variables of Interest:

- Classification
  - Age Group
  - Gender
  - Race
  - Ethnicity
  - Risk of Mortality
- Continuous
  - Total Costs
  - Length of Stay 
  - Total Charges

In [30]:
#Classification
df['mortality_sparcs'] = df['APR Risk of Mortality'].apply(lambda x: 'Minor' if x == 'Moderate' or x == 'Minor' else 'Major')
df.drop(columns=['APR Risk of Mortality'], axis=1, inplace=True)
df['mortality_sparcs'].value_counts()

Minor    18942
Major     4641
Name: mortality_sparcs, dtype: int64

In [33]:
x = df.drop(columns=['mortality_sparcs'])
y = df['mortality_sparcs']
x


Health Service Area Hospital County  ...  Total Charges  Total Costs
0              Western NY        Allegany  ...        4757.01      4747.83
1              Western NY        Allegany  ...        5090.25      2985.64
2              Western NY        Allegany  ...        4948.50      2129.67
3              Western NY        Allegany  ...        4719.75      8454.41
4              Western NY        Allegany  ...       50384.75     34565.03
...                   ...             ...  ...            ...          ...
23578         Long Island         Suffolk  ...       50833.00      8961.40
23579         Long Island         Suffolk  ...       10948.00      2214.06
23580         Long Island         Suffolk  ...       46421.00     11083.24
23581         Long Island         Suffolk  ...       46122.00      7951.26
23582         Long Island         Suffolk  ...       32225.00      6212.95

[23583 rows x 33 columns]

In [34]:
y

0        Minor
1        Minor
2        Minor
3        Minor
4        Major
         ...  
23578    Minor
23579    Minor
23580    Minor
23581    Major
23582    Major
Name: mortality_sparcs, Length: 23583, dtype: object

In [35]:
X_train, X_test, y_train, y_test = train_test_split(x,y,stratify=y,test_size=0.25)

In [38]:
automl = AutoML(
    results_path="sparcs_binary_mortality_risk",
    mode= "Explain"
)

In [39]:
automl.fit(X_train,y_train)

Linear algorithm was disabled.
AutoML directory: sparcs_binary_mortality_risk
The task is binary_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 0.495855 trained in 1.01 seconds


2_DecisionTree logloss 0.211062 trained in 17.01 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.189659 trained in 17.29 seconds
4_Default_NeuralNetwork logloss 0.223399 trained in 9.34 seconds
5_Default_RandomForest logloss 0.200805 trained in 28.87 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.188339 trained in 1.57 seconds
AutoML fit time: 87.5 seconds
AutoML best model: Ensemble


AutoML(results_path='sparcs_binary_mortality_risk')

In [41]:
predition = automl.predict(X_test)
predition

array(['Minor', 'Minor', 'Major', ..., 'Major', 'Minor', 'Minor'],
      dtype=object)

In [42]:
automl.report()

In [43]:
##Regression
df['Total Costs'].describe


<bound method NDFrame.describe of 0         4747.83
1         2985.64
2         2129.67
3         8454.41
4        34565.03
           ...   
23578     8961.40
23579     2214.06
23580    11083.24
23581     7951.26
23582     6212.95
Name: Total Costs, Length: 23583, dtype: float64>

In [45]:
x_without = df.drop(columns=['Total Costs'])
y_with = df['Total Costs']

In [46]:
x_without 

Health Service Area Hospital County  ...  Total Charges  mortality_sparcs
0              Western NY        Allegany  ...        4757.01             Minor
1              Western NY        Allegany  ...        5090.25             Minor
2              Western NY        Allegany  ...        4948.50             Minor
3              Western NY        Allegany  ...        4719.75             Minor
4              Western NY        Allegany  ...       50384.75             Major
...                   ...             ...  ...            ...               ...
23578         Long Island         Suffolk  ...       50833.00             Minor
23579         Long Island         Suffolk  ...       10948.00             Minor
23580         Long Island         Suffolk  ...       46421.00             Minor
23581         Long Island         Suffolk  ...       46122.00             Major
23582         Long Island         Suffolk  ...       32225.00             Major

[23583 rows x 33 columns]

In [47]:
y_with

0         4747.83
1         2985.64
2         2129.67
3         8454.41
4        34565.03
           ...   
23578     8961.40
23579     2214.06
23580    11083.24
23581     7951.26
23582     6212.95
Name: Total Costs, Length: 23583, dtype: float64

In [48]:
automl_2 = AutoML()
automl_2.fit(x_without,y_with)

Linear algorithm was disabled.
AutoML directory: AutoML_1
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline rmse 23541.268908 trained in 1.12 seconds
2_DecisionTree rmse 10272.122412 trained in 16.31 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost rmse 7121.41405 trained in 144.08 seconds
4_Default_NeuralNetwork rmse 11669.008933 trained in 7.57 seconds
5_Default_RandomForest rmse 10942.362427 trained in 19.1 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 6323.943924 trained in 0.31 seconds
AutoML fit time: 198.99 seconds
AutoML best model: Ensemble


AutoML()

In [49]:
automl_2.report()